In [24]:
import numpy as np
import matplotlib.pyplot as plt
import pandas
import math
import tensorflow as tf
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import mean_squared_error
from tensorflow.keras.models import Sequential
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Dense
from tensorflow.keras.layers import LSTM
from tensorflow.keras.layers import Dropout
from tensorflow.keras.layers import Input

In [15]:
# fix random seed for reproducibility
np.random.seed(7)

In [16]:
data_x = np.loadtxt('gesture_input_x_v11.csv', dtype=float)
data_y = np.loadtxt('gesture_input_y_v11.csv', dtype=float)

data_x.shape, data_y.shape

((314, 270), (314, 5))

In [17]:
# split into train and test sets
train_size = int(len(data_x) * 0.8)
test_size = len(data_x) - train_size
train_size, test_size

(251, 63)

In [18]:
train_x, test_x = data_x[0:train_size,:], data_x[train_size:,:]
train_y, test_y = data_y[0:train_size,:], data_y[train_size:,:]

# reshape input to be [samples, time steps, features]
train_x = np.reshape(train_x, (train_x.shape[0], 1, train_x.shape[1]))
test_x = np.reshape(test_x, (test_x.shape[0], 1, test_x.shape[1]))

train_x.shape, train_y.shape, test_x.shape, test_y.shape

((251, 1, 270), (251, 5), (63, 1, 270), (63, 5))

In [19]:
regularizer = tf.contrib.layers.l2_regularizer(scale=0.01)

In [29]:
input_tensor = Input(shape = (1, 270), name = "input_tensor")
lstm_layer = LSTM(270, activation=tf.nn.tanh, kernel_regularizer=regularizer)(input_tensor)
hidden_layer = Dense(100, activation=tf.nn.relu, kernel_regularizer=regularizer)(lstm_layer)
output_tensors = Dense(5, activation=tf.nn.softmax, name = "output_tensors")(hidden_layer)

model = Model(input_tensor, output_tensors)
model.compile(loss='mean_squared_error', optimizer='adam', metrics=['accuracy'])
model.summary()

estimator_model = tf.keras.estimator.model_to_estimator(keras_model = model, model_dir = './models')
# # create and fit the LSTM network
# model = Sequential()
# model.add(LSTM(270, activation=tf.nn.tanh, kernel_regularizer=regularizer, input_shape=(1, 270)))
# model.add(Dense(100, activation=tf.nn.relu, kernel_regularizer=regularizer))
# model.add(Dense(5, activation=tf.nn.softmax))

# model.compile(loss='mean_squared_error', optimizer='adam', metrics=['accuracy'])

# model.summary()

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_tensor (InputLayer)    (None, 1, 270)            0         
_________________________________________________________________
lstm_10 (LSTM)               (None, 270)               584280    
_________________________________________________________________
dense_4 (Dense)              (None, 100)               27100     
_________________________________________________________________
output_tensors (Dense)       (None, 5)                 505       
Total params: 611,885
Trainable params: 611,885
Non-trainable params: 0
_________________________________________________________________
INFO:tensorflow:Using default config.
INFO:tensorflow:Using the Keras model provided.
INFO:tensorflow:Using config: {'_model_dir': './models', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_sessio

In [30]:
def input_function(features,labels=None,shuffle=False):
    input_fn = tf.estimator.inputs.numpy_input_fn(
        x={"input_tensor": features},
        y=labels,
        shuffle=shuffle,
        batch_size = 10,
        num_epochs = 200
    )
    return input_fn
  
estimator_model.train(input_fn = input_function(train_x, train_y, False))

Instructions for updating:
To construct input pipelines, use the `tf.data` module.
Instructions for updating:
To construct input pipelines, use the `tf.data` module.
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Warm-starting with WarmStartSettings: WarmStartSettings(ckpt_to_initialize_from='./models/keras/keras_model.ckpt', vars_to_warm_start='.*', var_name_to_vocab_info={}, var_name_to_prev_var_name={})
INFO:tensorflow:Warm-starting from: ('./models/keras/keras_model.ckpt',)
INFO:tensorflow:Warm-starting variable: lstm_10/kernel; prev_var_name: Unchanged
INFO:tensorflow:Warm-starting variable: lstm_10/recurrent_kernel; prev_var_name: Unchanged
INFO:tensorflow:Warm-starting variable: lstm_10/bias; prev_var_name: Unchanged
INFO:tensorflow:Warm-starting variable: dense_4/kernel; prev_var_name: Unchanged
INFO:tensorflow:Warm-starting variable: dense_4/bias; prev_var_name: Unchanged
INFO:tensorflow:Warm-starting variable: output_tensors/kernel; p

INFO:tensorflow:global_step/sec: 259.435
INFO:tensorflow:loss = 0.083470255, step = 3701 (0.386 sec)
INFO:tensorflow:global_step/sec: 255.715
INFO:tensorflow:loss = 0.0812392, step = 3801 (0.391 sec)
INFO:tensorflow:global_step/sec: 261.023
INFO:tensorflow:loss = 0.10705663, step = 3901 (0.383 sec)
INFO:tensorflow:global_step/sec: 261.935
INFO:tensorflow:loss = 0.15497762, step = 4001 (0.382 sec)
INFO:tensorflow:global_step/sec: 266.894
INFO:tensorflow:loss = 0.11178172, step = 4101 (0.374 sec)
INFO:tensorflow:global_step/sec: 277.852
INFO:tensorflow:loss = 0.07016843, step = 4201 (0.360 sec)
INFO:tensorflow:global_step/sec: 284.878
INFO:tensorflow:loss = 0.06863642, step = 4301 (0.351 sec)
INFO:tensorflow:global_step/sec: 270.176
INFO:tensorflow:loss = 0.09622084, step = 4401 (0.370 sec)
INFO:tensorflow:global_step/sec: 269.249
INFO:tensorflow:loss = 0.08306375, step = 4501 (0.371 sec)
INFO:tensorflow:global_step/sec: 276.029
INFO:tensorflow:loss = 0.08555045, step = 4601 (0.362 sec)


In [31]:
def freeze_graph(model_dir, output_node_names):
  """Extract the sub graph defined by the output nodes and convert 
  all its variables into constant 
  Args:
      model_dir: the root folder containing the checkpoint state file
      output_node_names: a string, containing all the output node's names, 
                          comma separated"""
  if not tf.gfile.Exists(model_dir):
    raise AssertionError(
      "Export directory doesn't exists. Please specify an export "
      "directory: %s" % model_dir)

  if not output_node_names:
    print("You need to supply the name of a node to --output_node_names.")
    return -1

  # We retrieve our checkpoint fullpath
  checkpoint = tf.train.get_checkpoint_state(model_dir)
  input_checkpoint = checkpoint.model_checkpoint_path
    
  # We precise the file fullname of our freezed graph
  absolute_model_dir = "/".join(input_checkpoint.split('/')[:-1])
  output_graph = absolute_model_dir + "/frozen_model.pb"

  # We clear devices to allow TensorFlow to control on which device it will load operations
  clear_devices = True

  # We start a session using a temporary fresh Graph
  with tf.Session(graph=tf.Graph()) as sess:
    # We import the meta graph in the current default Graph
    saver = tf.train.import_meta_graph(input_checkpoint + '.meta', clear_devices=clear_devices)

    # We restore the weights
    saver.restore(sess, input_checkpoint)

    # We use a built-in TF helper to export variables to constants
    output_graph_def = tf.graph_util.convert_variables_to_constants(
      sess, # The session is used to retrieve the weights
      tf.get_default_graph().as_graph_def(), # The graph_def is used to retrieve the nodes 
      output_node_names.split(",") # The output node names are used to select the usefull nodes
    ) 

    # Finally we serialize and dump the output graph to the filesystem
    with tf.gfile.GFile(output_graph, "wb") as f:
      f.write(output_graph_def.SerializeToString())
    print("%d ops in the final graph." % len(output_graph_def.node))

  return output_graph_def

In [32]:
freeze_graph('./models/',"output_tensors/Softmax")

Instructions for updating:
Use standard file APIs to check for files with this prefix.
INFO:tensorflow:Restoring parameters from ./models/model.ckpt-5021
Instructions for updating:
Use tf.compat.v1.graph_util.convert_variables_to_constants
Instructions for updating:
Use tf.compat.v1.graph_util.extract_sub_graph
INFO:tensorflow:Froze 7 variables.
INFO:tensorflow:Converted 7 variables to const ops.
214 ops in the final graph.


node {
  name: "enqueue_input/fifo_queue"
  op: "FIFOQueueV2"
  attr {
    key: "capacity"
    value {
      i: 1000
    }
  }
  attr {
    key: "component_types"
    value {
      list {
        type: DT_INT64
        type: DT_DOUBLE
        type: DT_DOUBLE
      }
    }
  }
  attr {
    key: "container"
    value {
      s: ""
    }
  }
  attr {
    key: "shapes"
    value {
      list {
        shape {
        }
        shape {
          dim {
            size: 1
          }
          dim {
            size: 270
          }
        }
        shape {
          dim {
            size: 5
          }
        }
      }
    }
  }
  attr {
    key: "shared_name"
    value {
      s: ""
    }
  }
}
node {
  name: "fifo_queue_DequeueUpTo/n"
  op: "Const"
  attr {
    key: "dtype"
    value {
      type: DT_INT32
    }
  }
  attr {
    key: "value"
    value {
      tensor {
        dtype: DT_INT32
        tensor_shape {
        }
        int_val: 10
      }
    }
  }
}
node {
  name: "fifo_q

In [27]:
history = model.fit(train_x, train_y, epochs=200, batch_size=10, verbose=1)

Instructions for updating:
Use tf.cast instead.
Epoch 1/200
251/251 [==============================] - 1s 3ms/sample - loss: 1.9982 - acc: 0.2988
Epoch 2/200
251/251 [==============================] - 0s 446us/sample - loss: 0.7575 - acc: 0.3665
Epoch 3/200
251/251 [==============================] - 0s 458us/sample - loss: 0.3598 - acc: 0.3705
Epoch 4/200
251/251 [==============================] - 0s 465us/sample - loss: 0.2310 - acc: 0.4223
Epoch 5/200
251/251 [==============================] - 0s 459us/sample - loss: 0.1849 - acc: 0.3785
Epoch 6/200
251/251 [==============================] - 0s 470us/sample - loss: 0.1661 - acc: 0.3745
Epoch 7/200
251/251 [==============================] - 0s 454us/sample - loss: 0.1550 - acc: 0.4382
Epoch 8/200
251/251 [==============================] - 0s 502us/sample - loss: 0.1496 - acc: 0.4661
Epoch 9/200
251/251 [==============================] - 0s 511us/sample - loss: 0.1501 - acc: 0.4064
Epoch 10/200
251/251 [==============================] 

251/251 [==============================] - 0s 456us/sample - loss: 0.0940 - acc: 0.7530
Epoch 80/200
251/251 [==============================] - 0s 448us/sample - loss: 0.0973 - acc: 0.7570
Epoch 81/200
251/251 [==============================] - 0s 460us/sample - loss: 0.0982 - acc: 0.7410
Epoch 82/200
251/251 [==============================] - 0s 454us/sample - loss: 0.0958 - acc: 0.7410
Epoch 83/200
251/251 [==============================] - 0s 458us/sample - loss: 0.0959 - acc: 0.7570
Epoch 84/200
251/251 [==============================] - 0s 471us/sample - loss: 0.0895 - acc: 0.7689
Epoch 85/200
251/251 [==============================] - 0s 437us/sample - loss: 0.0938 - acc: 0.7410
Epoch 86/200
251/251 [==============================] - 0s 462us/sample - loss: 0.0932 - acc: 0.7689
Epoch 87/200
251/251 [==============================] - 0s 463us/sample - loss: 0.0919 - acc: 0.8048
Epoch 88/200
251/251 [==============================] - 0s 451us/sample - loss: 0.0912 - acc: 0.7809
Epo

251/251 [==============================] - 0s 422us/sample - loss: 0.0783 - acc: 0.8247
Epoch 160/200
251/251 [==============================] - 0s 425us/sample - loss: 0.0866 - acc: 0.7809
Epoch 161/200
251/251 [==============================] - 0s 425us/sample - loss: 0.0796 - acc: 0.8327
Epoch 162/200
251/251 [==============================] - 0s 422us/sample - loss: 0.0828 - acc: 0.8167
Epoch 163/200
251/251 [==============================] - 0s 419us/sample - loss: 0.0822 - acc: 0.8088
Epoch 164/200
251/251 [==============================] - 0s 427us/sample - loss: 0.0858 - acc: 0.8127
Epoch 165/200
251/251 [==============================] - 0s 424us/sample - loss: 0.0791 - acc: 0.8327
Epoch 166/200
251/251 [==============================] - 0s 424us/sample - loss: 0.0770 - acc: 0.8367
Epoch 167/200
251/251 [==============================] - 0s 429us/sample - loss: 0.0974 - acc: 0.7570
Epoch 168/200
251/251 [==============================] - 0s 434us/sample - loss: 0.0854 - acc: 0

In [11]:
model.evaluate(test_x, test_y)

63/63 [==============================] - 0s 1ms/sample - loss: 0.0901 - acc: 0.7778


[0.09006256763897245, 0.7777778]

In [ ]:
# Plot training & validation accuracy values
plt.plot(history.history['acc'])
plt.title('Model accuracy')
plt.ylabel('Accuracy')
plt.xlabel('Epoch')
plt.legend(['Train'], loc='upper left')
plt.show()

In [ ]:
model.predict(test_x[10].reshape(1, 1, 270))

In [ ]:
def freeze_session(session, keep_var_names=None, output_names=None, clear_devices=True):
    """
    Freezes the state of a session into a pruned computation graph.

    Creates a new computation graph where variable nodes are replaced by
    constants taking their current value in the session. The new graph will be
    pruned so subgraphs that are not necessary to compute the requested
    outputs are removed.
    @param session The TensorFlow session to be frozen.
    @param keep_var_names A list of variable names that should not be frozen,
                          or None to freeze all the variables in the graph.
    @param output_names Names of the relevant graph outputs.
    @param clear_devices Remove the device directives from the graph for better portability.
    @return The frozen graph definition.
    """
    graph = session.graph
    with graph.as_default():
        freeze_var_names = list(set(v.op.name for v in tf.global_variables()).difference(keep_var_names or []))
        output_names = output_names or []
        output_names += [v.op.name for v in tf.global_variables()]
        input_graph_def = graph.as_graph_def()
        if clear_devices:
            for node in input_graph_def.node:
                node.device = ""
        frozen_graph = tf.graph_util.convert_variables_to_constants(
            session, input_graph_def, output_names, freeze_var_names)
        return frozen_graph

In [ ]:
# Save model in pb format
frozen_graph = freeze_session(tf.keras.backend.get_session(), output_names=[out.op.name for out in model.outputs])
tf.train.write_graph(frozen_graph, "models", "lstm_gestures.pb", as_text=False)